# Kalman Filter Example

In [32]:
import sys
sys.path.append('../../')
import numpy as np
from veroku.factors.gaussian import Gaussian, GaussianMixture
from veroku.cluster_graph import ClusterGraph

In [33]:
def make_linear_gaussian(A, N, conditioning_var_templates, conditional_var_templates):
    X_dim = len(conditioning_var_templates)
    Sxx = np.eye(X_dim)
    Kxx = np.linalg.inv(Sxx)

    ux = np.zeros([X_dim,1])
    hx = Kxx@ux
    
    S = np.block([[Sxx,    Sxx@A.T],
                  [A@Sxx,  A@Sxx@A.T+N]])
    K_joint = np.linalg.inv(S)
    K_cpd = K_joint.copy()
    K_cpd[:X_dim,:X_dim] = K_cpd[:X_dim,:X_dim] - Kxx

    mean_joint = np.block([[ux],[A.T@ux]])

    h_joint = K_joint@mean_joint
    h_cpd = h_joint.copy()
    h_cpd[:X_dim] = h_cpd[:X_dim] - ux
    
    #print('K_cpd = ', K_cpd)
    var_names=conditioning_var_templates+conditional_var_templates
    
    return Gaussian(var_names=var_names, K=K_cpd, h=h_cpd, g=0.0)
    

def make_linear_gaussian_cpd_template(A, N, conditioning_var_templates, conditional_var_templates):
    assert len(conditioning_var_templates) == A.shape[0]
    assert N.shape[0] == A.shape[0]
    nlg = make_linear_gaussian(A, N, conditioning_var_templates, conditional_var_templates)
    var_templates = conditioning_var_templates+conditional_var_templates
    gaussian_parameters = {'K':nlg.get_K(), 'h':nlg.get_h(), 'g':0}
    return GaussianTemplate(gaussian_parameters, var_templates)


In [34]:
#A = np.array([[1, 0],
#              [0, 1]])
#N = np.eye(2)
#make_linear_gaussian(A, N, ['a', 'b'], ['c', 'd'])

In [35]:
from veroku.factors._factor_template import FactorTemplate
class GaussianTemplate(FactorTemplate):

    def __init__(self, gaussian_parameters, var_templates):
        """
        Create a Categorical factor template.

        :param log_probs_table: The log_probs_table that specifies the assignments and values for the template.
        :type log_probs_table: tuple:float dict
        :param var_templates: A list of formattable strings.
        :type var_templates: str list

        >>>gaussian_parameters = {'K': np.array([1,0][0,1]]),
        >>>                       'h': np.array([0][1]]),
        >>>                       'g': 0}
        """
        # TODO: Complete and improve docstring.
        super().__init__(var_templates=var_templates)
        self.K = gaussian_parameters['K']
        self.h = gaussian_parameters['h']        
        self.g = gaussian_parameters['g']
        

    def make_factor(self, format_dict=None, var_names=None):
        """
        Make a factor with var_templates formatted by format_dict to create specific var names.

        :param format_dict: The dictionary to be used to format the var_templates strings.
        :type format_dict: str dict
        :return: The instantiated factor.
        :rtype: Categorical
        """
        if format_dict is not None:
            assert var_names is None
            var_names = [vt.format(**format_dict) for vt in self._var_templates]
        # TODO: remove this and find better solution
        g = Gaussian(K=self.K.copy(), h=self.h.copy(), g=self.g, var_names=var_names)
        g._is_vacuous = True
        return g


In [64]:
X_now_var_templates = ['Xsx_{t_now}','Xsy_{t_now}','Xvx_{t_now}','Xvy_{t_now}']
X_nxt_var_templates = ['Xsx_{t_nxt}','Xsy_{t_nxt}','Xvx_{t_nxt}','Xvy_{t_nxt}']
Y_now_var_templates = ['Ysx_{t_now}','Ysy_{t_now}','Yvx_{t_now}','Yvy_{t_now}']

X_dim = len(X_now_var_templates)

dt = 10.1
A_X_now_X_nxt = np.array([[1, 0, dt, 0],
                          [0, 1, 0,  dt],
                          [0, 0, 1,  0],
                          [0, 0, 0,  1]])
A_X_now_Y_now = np.array([[1, 0, 0, 0],
                          [0, 1, 0, 0],
                          [0, 0, 1, 0],
                          [0, 0, 0, 1]])
N_Y = np.array([[3, 0, 0, 0],
                [0, 3, 0, 0],
                [0, 0, 2, 0],
                [0, 0, 0, 2]])*0.1
N_X = np.array([[0.1, 0, 0, 0],
                [0, 0.1, 0, 0],
                [0, 0, 0.2, 0],
                [0, 0, 0, 0.2]])*0.1
X_now_X_nxt_template = make_linear_gaussian_cpd_template(A_X_now_X_nxt,
                                                         N_X,
                                                         X_now_var_templates,
                                                         X_nxt_var_templates)
X_now_Y_now_template = make_linear_gaussian_cpd_template(A_X_now_Y_now,
                                                         N_Y,
                                                         X_now_var_templates,
                                                         Y_now_var_templates)

X_prior_var_format_dict = {'t_now':0}
X_prior_vars = [vt.format(**X_prior_var_format_dict) for vt in X_now_var_templates]

X_prior = Gaussian(cov=np.eye(X_dim), mean=np.zeros([X_dim, 1]), log_weight=0.0, var_names=X_prior_vars)
factors = [X_prior]

# data generation
system_state = X_prior.get_mean()
dummy_var_names = [str(i) for i in range(X_dim)]
measurement_noise_distribution = Gaussian(mean=np.zeros([X_dim, 1]), cov=N_Y, log_weight=0,var_names=dummy_var_names)



num_time_steps = 50
evidence_dict = {}
for timestep in range(num_time_steps):
    var_format_dict = {'t_now':timestep,'t_nxt':timestep+1}
    
    XX_factor = X_now_X_nxt_template.make_factor(var_format_dict)
    factors.append(XX_factor)
    if (timestep > 0) and (timestep < num_time_steps-1):
        XY_factor = X_now_Y_now_template.make_factor(var_format_dict)
        factors.append(XY_factor)
        Y_now_vars = [vt.format(**var_format_dict) for vt in Y_now_var_templates]
        Y_now_values = (system_state + measurement_noise_distribution.sample(1)).ravel().tolist()
        observations_now = {var_name:value for var_name, value in zip(Y_now_vars, Y_now_values)}
        #print('observations_now:\n', observations_now)
        evidence_dict.update(observations_now)
    
    system_state = A_X_now_X_nxt.T@system_state


In [65]:
Kalman_filter_cg = ClusterGraph(factors=factors, special_evidence=evidence_dict, make_animation_gif=False, debug=True)

../../veroku/cluster_graph.py:94: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray
  data = np.array([keys, values]).T


In [66]:
Kalman_filter_cg.show()

In [67]:
factors = [c._factor for c in Kalman_filter_cg._clusters]

In [69]:
#joint = factors[0]
#for f in factors[1:]:
#    joint = joint.absorb(f)


In [70]:
#for i in range(len(factors)-2):
#    var_format_dict = {'i':i}
#    var_templates = ['Xsx_{i}', 'Xsy_{i}']
#    var_names = [vt.format(**var_format_dict) for vt in var_templates]
#    marg = joint.marginalize(var_names, keep=True)
#    print('\n\n\n')
#    marg.show(update_covform=True, show_canform=False)
#    
#joint.show()

In [71]:
Kalman_filter_cg.process_graph(max_iter=220, sync=True)

Info: Starting iterative message passing.*


In [73]:
Kalman_filter_cg.plot_message_convergence()

In [74]:
from matplotlib.patches import Ellipse
import matplotlib
import matplotlib.pyplot as plt
import copy


def get_kalman_filter_position_posteriors(kf_cg, num_timesteps, pos_dim, X_var_templates, verbose=False):
    # Note: here we assume that the position variables start at 0
    single_space_var_names = None
    marginals = []
    means = []
    for i in range(num_timesteps-10):
        X_var_format_dict = {'t_now':i}
        X_vars = [vt.format(**X_var_format_dict) for vt in X_var_templates]
        #print('X_vars: ', X_vars)
        X_pos_vars = X_vars[0:pos_dim]
        if single_space_var_names is None:
            single_space_var_names = X_pos_vars
        
        pos_marginal = kf_cg.get_marginal(X_pos_vars)
        if verbose:
            print('\n\n')
            #pos_marginal.show(update_covform=False, show_canform=True)
            pos_marginal.show(update_covform=True, show_canform=False)
        
        # make var names the same (they are the same except at different time steps) to be able to plot in single space.
        pos_marginal._var_names = copy.deepcopy(single_space_var_names)
        
        
        pos_mean = pos_marginal.get_mean()
        means.append(pos_mean)
        marginals.append(pos_marginal)
        #if i > 2:
        #    break
    return marginals

def get_ellipse_patch(ax, cov, mean):
    eigen_values_array, eigen_vectors_array = np.linalg.eig(cov)
    max_len_eig_vector = eigen_vectors_array[:, np.argmax(eigen_values_array)]
    angle = np.arctan2(max_len_eig_vector[1],max_len_eig_vector[0])
    
    width  = eigen_values_array[0]
    height  = eigen_values_array[1]

    ellipse = matplotlib.patches.Ellipse(mean,
                                         width,
                                         height,
                                         angle=angle,
                                         fc=(1,0,0,0),
                                         ec = (0,0,0,1),
                                         lw=2)
    return ellipse

def add_ellipse(ax, ellipse):
    ax.add_patch(ellipse)


def get_2d_std_dev_ellipses(gaussians):
    ellipse_patches = []
    for g in gaussians:
        ellipse_patch = get_ellipse_patch(ax, g.get_cov(), g.get_mean())
        ellipse_patches.append(ellipse_patch)
    return ellipse_patches

def plot_2d_std_dev_ellipses(gaussians):
    fig = plt.figure()
    ax = fig.add_subplot(1, 1, 1)
    patches = get_2d_std_dev_ellipses(gaussians)
    for patch in patches:
        ax.add_patch(patch)
    ax.autoscale()

In [75]:
position_posteriors = get_kalman_filter_position_posteriors(kf_cg=Kalman_filter_cg,
                                                            num_timesteps=num_time_steps,
                                                            pos_dim=2,
                                                            X_var_templates=X_now_var_templates,
                                                            verbose=True)





vars =  ['Xsx_0', 'Xsy_0']
Cov = 
 [[0.7556 0.    ]
 [0.     0.7556]]
mean = 
 [[0.1416]
 [0.0809]]
log_weight = 
 -75.0211440669743
is_vacuous:  False



vars =  ['Xsx_1', 'Xsy_1']
Cov = 
 [[0.2119 0.    ]
 [0.     0.2119]]
mean = 
 [[-0.0071]
 [ 0.4378]]
log_weight = 
 -75.02114406697451
is_vacuous:  False



vars =  ['Xsx_2', 'Xsy_2']
Cov = 
 [[0.2338 0.    ]
 [0.     0.2338]]
mean = 
 [[-0.6222]
 [ 0.6138]]
log_weight = 
 -72.92438180380928
is_vacuous:  False



vars =  ['Xsx_3', 'Xsy_3']
Cov = 
 [[0.2453 0.    ]
 [0.     0.2453]]
mean = 
 [[0.1063]
 [0.1647]]
log_weight = 
 -70.78968019946085
is_vacuous:  False



vars =  ['Xsx_4', 'Xsy_4']
Cov = 
 [[0.2517 0.    ]
 [0.     0.2517]]
mean = 
 [[ 0.0187]
 [-0.2436]]
log_weight = 
 -67.06533819010828
is_vacuous:  False



vars =  ['Xsx_5', 'Xsy_5']
Cov = 
 [[0.2557 0.    ]
 [0.     0.2557]]
mean = 
 [[-0.0317]
 [ 0.0835]]
log_weight = 
 -63.50157595888055
is_vacuous:  False



vars =  ['Xsx_6', 'Xsy_6']
Cov = 
 [[0.2605 0.    ]
 [

In [77]:
#plot_2d_std_dev_ellipses(position_posteriors)

In [78]:
#https://kapernikov.com/ipywidgets-with-matplotlib/
%matplotlib widget
import ipywidgets as widgets
import matplotlib.pyplot as plt
import numpy as np

# set up plot
fig, ax = plt.subplots(figsize=(6, 4))
ax.set_ylim([-10, 10])
ax.set_xlim([-10, 10])
ax.grid(True)
 
ellipse_patches = get_2d_std_dev_ellipses(position_posteriors) 
last_timestep_index = len(ellipse_patches)-1
@widgets.interact(t=(0, last_timestep_index, 1))
def update(t = 0):
    """Remove old lines from plot and plot new one"""
    [l.remove() for l in ax.patches]
    ax.add_patch(ellipse_patches[t])

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

interactive(children=(IntSlider(value=0, description='t', max=39), Output()), _dom_classes=('widget-interact',…